In [158]:
# 패키지 로드
import warnings
warnings.filterwarnings('ignore')

import numpy as np
import pandas as pd
from tqdm.notebook import tqdm
from sklearn.model_selection import train_test_split
from collections import defaultdict
import os, random

from scipy import sparse
from sklearn.preprocessing import LabelEncoder
import matplotlib.pyplot as plt
%matplotlib inline

import torch
import torch.nn as nn
from torch.nn.init import normal_
from torch.utils.data import TensorDataset, DataLoader
import torch.nn.functional as F

from datetime import datetime
from datetime import timedelta

In [2]:
# 경로 설정
data_path = '../data'
saved_path = './saved'
output_path = './submission'

In [3]:
#bd = pd.read_csv('buy_data.csv')
#hd = pd.read_csv('history_data.csv')
mdp = pd.read_csv('meta_data_plus.csv')
md = pd.read_csv('meta_data.csv')
#prd = pd.read_csv('profile_data.csv')
#sd = pd.read_csv('search_data.csv')
#wd = pd.read_csv('watch_e_data.csv')
#ss = pd.read_csv('sample_submission.csv')

In [4]:
# 데이터 불러오기 
history = pd.read_csv(os.path.join(data_path, 'history_data.csv'), encoding='utf-8')
watch = pd.read_csv(os.path.join(data_path, 'watch_e_data.csv'), encoding='utf-8')
buy = pd.read_csv(os.path.join(data_path, 'buy_data.csv'), encoding='utf-8') 
search = pd.read_csv(os.path.join(data_path, 'search_data.csv'), encoding='utf-8')
profile = pd.read_csv(os.path.join(data_path, 'profile_data.csv'), encoding='utf-8')

In [5]:
hd = history.copy()
wd = watch.copy()
bd = buy.copy()
sd = search.copy()
pd = profile.copy()

In [6]:
print('hd 데이터(중복 제거 전) : ', hd.shape)
print('wd 데이터(중복 제거 전) : ', wd.shape)

hd 데이터(중복 제거 전) :  (1005651, 8)
wd 데이터(중복 제거 전) :  (892794, 8)


#### 1. 중복 데이터 제거

In [7]:
# 중복행 확인
hd[hd.duplicated()] # 시청시작 데이터

profile_id           ss_id        log_time act_target_dtl  album_id  \
517               5  20220421082427  20220421082957        MKID003        92   
519               5  20220421082427  20220421085009        MKID003       174   
521               5  20220421082427  20220421090237        MKID003       201   
523               5  20220421082427  20220421090332        MKID003       187   
525               5  20220421082427  20220421090449        MKID003       305   
...             ...             ...             ...            ...       ...   
1004498       32908  20220420203843  20220420204139        MKID003      6458   
1005467       33015  20220424194027  20220424194036        MKID003       416   
1005469       33015  20220424194027  20220424194091        MKID003       175   
1005471       33015  20220424195608  20220424195612        MKID003        57   
1005473       33015  20220424195608  20220424195955        MKID003      2502   

         payment continuous_play short_trailer  
517          NaN               N             N  
519          NaN               N             N  
521          NaN               N             N  
523          NaN               N             N  
525          NaN               N             N  
...          ...             ...           ...  
1004498      NaN               N             N  
1005467      NaN               Y             N  
1005469      NaN               N             Y  
1005471      NaN               N             N  
1005473      NaN               N             N  

[106378 rows x 8 columns]

In [8]:
wd[wd.duplicated()] # 시청종료 데이터

profile_id           ss_id        log_time act_target_dtl  album_id  \
507              5  20220421082427  20220421082953        MKID049       298   
509              5  20220421082427  20220421085005        MKID049        92   
511              5  20220421082427  20220421090233        MKID049       174   
513              5  20220421082427  20220421090327        MKID049       201   
515              5  20220421082427  20220421090443        MKID049       187   
...            ...             ...             ...            ...       ...   
892571       33016  20220424194881  20220424195327        MKID049      5873   
892573       33016  20220424194881  20220424195543        MKID049      5874   
892575       33016  20220424194881  20220424195570        MKID049      5874   
892577       33016  20220424194881  20220424195683        MKID049      4598   
892579       33016  20220424200269  20220424200655        MKID049       267   

        watch_time  total_time  continuous_play  
507            307         309                1  
509           1207        1207                1  
511            744         745                1  
513             50          50                1  
515             70          70                1  
...            ...         ...              ...  
892571          94          94                1  
892573          94          94                1  
892575          50          94                0  
892577          34          95                0  
892579           0          88                0  

[92054 rows x 8 columns]

In [9]:
# 중복행 제거
hd = hd[~hd.duplicated()]
print('hd 데이터(중복 제거 후) : ', hd.shape)

wd = wd[~wd.duplicated()]
print('wd 데이터(중복 제거 후) : ', wd.shape)

hd 데이터(중복 제거 후) :  (899273, 8)
wd 데이터(중복 제거 후) :  (800740, 8)


#### 2. 이상치 제거

#### 2-1. History_data 내 log_time 이상치 제거

In [10]:
hd.head()

profile_id           ss_id        log_time act_target_dtl  album_id  \
0           3  20220301115653  20220301115719        MKID003        15   
1           3  20220301115653  20220301115809        MKID003        16   
2           3  20220301115653  20220301115958        MKID003        17   
3           3  20220301115653  20220301120118        MKID003        18   
4           3  20220301115653  20220301120229        MKID003        19   

   payment continuous_play short_trailer  
0      NaN               Y             N  
1      NaN               Y             N  
2      NaN               Y             N  
3      NaN               Y             N  
4      NaN               Y             N

In [11]:
# log_time 날짜/시간 분리
hd["log_time"] = hd["log_time"].astype(str)
hd["date"] = hd["log_time"].str.slice(0, 8)
hd["time"] = hd["log_time"].str.slice(8, 14)

In [12]:
hd.head()

profile_id           ss_id        log_time act_target_dtl  album_id  \
0           3  20220301115653  20220301115719        MKID003        15   
1           3  20220301115653  20220301115809        MKID003        16   
2           3  20220301115653  20220301115958        MKID003        17   
3           3  20220301115653  20220301120118        MKID003        18   
4           3  20220301115653  20220301120229        MKID003        19   

   payment continuous_play short_trailer      date    time  
0      NaN               Y             N  20220301  115719  
1      NaN               Y             N  20220301  115809  
2      NaN               Y             N  20220301  115958  
3      NaN               Y             N  20220301  120118  
4      NaN               Y             N  20220301  120229

In [13]:
hd.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 899273 entries, 0 to 1005650
Data columns (total 10 columns):
 #   Column           Non-Null Count   Dtype  
---  ------           --------------   -----  
 0   profile_id       899273 non-null  int64  
 1   ss_id            899273 non-null  int64  
 2   log_time         899273 non-null  object 
 3   act_target_dtl   899273 non-null  object 
 4   album_id         899273 non-null  int64  
 5   payment          59193 non-null   float64
 6   continuous_play  899273 non-null  object 
 7   short_trailer    899273 non-null  object 
 8   date             899273 non-null  object 
 9   time             899273 non-null  object 
dtypes: float64(1), int64(3), object(6)
memory usage: 75.5+ MB


In [14]:
# 월 조건 (3 ~ 7월 제외한 월이 있는지)
con1 = (hd['date'].str[4:6] != '03')
con2 = (hd['date'].str[4:6] != '04')
con3 = (hd['date'].str[4:6] != '05')
con4 = (hd['date'].str[4:6] != '06')
con5 = (hd['date'].str[4:6] != '07')

# 일 조건 (0일 / 00일 / 32일 이상 있는지)
con8 = (hd['date'].str[6:8] == '0')
con9 = (hd['date'].str[6:8] == '00')
con10 = (hd['date'].str[6:8].astype(int) >= 32)

In [15]:
print('조건에 맞지 않는 연도 수:', len(hd.loc[hd['date'].str[:4] != '2022']))
print('조건에 맞지 않는 월 수:', len(hd.loc[con1 & con2 & con3 & con4 & con5]))
print('조건에 맞지 않는 일 수:', len(hd.loc[con8 | con9 | con10]))

조건에 맞지 않는 연도 수: 0
조건에 맞지 않는 월 수: 0
조건에 맞지 않는 일 수: 0


In [16]:
print('조건에 맞지 않는 시 수:', len(hd.loc[hd['time'].str[:2] >= '24']))
print('조건에 맞지 않는 분 수:', len(hd.loc[hd['time'].str[2:4] >= '60']))
print('조건에 맞지 않는 초 수:', len(hd.loc[hd['time'].str[4:6] >= '60']))

조건에 맞지 않는 시 수: 0
조건에 맞지 않는 분 수: 0
조건에 맞지 않는 초 수: 73581


In [17]:
# 초에만 이상 있음
# 이상 있는 데이터 73,581개
hd.loc[hd['time'].str[4:6] >= '60']

profile_id           ss_id        log_time act_target_dtl  album_id  \
2975             30  20220305130048  20220305131273        MKID003      1901   
2976             30  20220305130048  20220305132966        MKID003      1902   
2978             30  20220305130048  20220305134092        MKID003      1903   
2983             30  20220320140092  20220320140174        MKID003       446   
2988             30  20220320140092  20220320144788        MKID003      1908   
...             ...             ...             ...            ...       ...   
1005638       33032  20220427151499  20220427154870        MKID003      7105   
1005639       33032  20220427151499  20220427155075        MKID003      1725   
1005646       33032  20220427155091  20220427155668        MKID003       381   
1005647       33032  20220427155091  20220427155680        MKID003       381   
1005650       33032  20220427155865  20220427155891        MKID003       381   

         payment continuous_play short_trailer      date    time  
2975         NaN               Y             N  20220305  131273  
2976         NaN               Y             N  20220305  132966  
2978         NaN               Y             N  20220305  134092  
2983       500.0               N             N  20220320  140174  
2988       500.0               Y             N  20220320  144788  
...          ...             ...           ...       ...     ...  
1005638      NaN               N             N  20220427  154870  
1005639      NaN               Y             N  20220427  155075  
1005646      NaN               Y             N  20220427  155668  
1005647      NaN               Y             N  20220427  155680  
1005650      NaN               N             N  20220427  155891  

[73581 rows x 10 columns]

In [18]:
# 이상 데이터 제거
hd = hd.drop(hd.loc[hd['time'].str[4:6] >= '60'].index)
print('이상 데이터 제거 후:', len(hd))

이상 데이터 제거 후: 825692


In [19]:
print('조건에 맞지 않는 초 수:', len(hd.loc[hd['time'].str[4:6] >= '60']))

조건에 맞지 않는 초 수: 0


#### 3. 결측치 제거 (payment Nan 값을 0으로)

In [20]:
# 결측치 확인
# wd, bd, pd에는 결측치x / pd keyword에 결측치 존재
hd.isnull().sum()

profile_id              0
ss_id                   0
log_time                0
act_target_dtl          0
album_id                0
payment            776209
continuous_play         0
short_trailer           0
date                    0
time                    0
dtype: int64

In [21]:
hd.replace(np.nan,0,inplace = True)

In [22]:
hd.isnull().sum()

profile_id         0
ss_id              0
log_time           0
act_target_dtl     0
album_id           0
payment            0
continuous_play    0
short_trailer      0
date               0
time               0
dtype: int64

In [23]:
hd.head()

profile_id           ss_id        log_time act_target_dtl  album_id  \
0           3  20220301115653  20220301115719        MKID003        15   
1           3  20220301115653  20220301115809        MKID003        16   
2           3  20220301115653  20220301115958        MKID003        17   
3           3  20220301115653  20220301120118        MKID003        18   
4           3  20220301115653  20220301120229        MKID003        19   

   payment continuous_play short_trailer      date    time  
0      0.0               Y             N  20220301  115719  
1      0.0               Y             N  20220301  115809  
2      0.0               Y             N  20220301  115958  
3      0.0               Y             N  20220301  120118  
4      0.0               Y             N  20220301  120229

In [24]:
hd.to_csv("pre_hd.csv")

#### 4. 파생변수 (선호도) 

In [57]:
wd.tail()

profile_id           ss_id        log_time act_target_dtl  album_id  \
892789       33032  20220427155091  20220427155653        MKID049       381   
892790       33032  20220427155091  20220427155694        MKID049       381   
892791       33032  20220427155839  20220427155826        MKID049       125   
892792       33032  20220427155706  20220427155836        MKID049       125   
892793       33032  20220427155839  20220427155897        MKID049       381   

        watch_time  total_time  continuous_play  
892789         463         464                1  
892790         462         463                1  
892791          10         520                0  
892792           6         521                0  
892793         462         464                1

In [36]:
#컬럼추가

wd_prefer = wd.copy()
wd_prefer['prefer'] = np.nan
wd_prefer.head()

profile_id           ss_id        log_time act_target_dtl  album_id  \
0           3  20220301115653  20220301115805        MKID049        15   
1           3  20220301115653  20220301115954        MKID049        16   
2           3  20220301115653  20220301120114        MKID049        17   
3           3  20220301115653  20220301120226        MKID049        18   
4           3  20220301115653  20220301120400        MKID049        19   

   watch_time  total_time  continuous_play  prefer  
0          46          46                1     NaN  
1         104         105                1     NaN  
2          76          76                1     NaN  
3          67          68                1     NaN  
4          90          90                0     NaN

In [98]:
#조건걸어서
#새컬럼에 값추가 1 ~ 4

for i in wd_prefer.index : 
    
    try : 
        #wd_prefer_check = wd_prefer.iloc[i]
        if wd_prefer.loc[i].watch_time < wd_prefer.loc[i].total_time * 0.25 :
            wd_prefer.loc[i,'prefer'] = 1
        elif wd_prefer.loc[i].watch_time < wd_prefer.loc[i].total_time * 0.5 :
            wd_prefer.loc[i,'prefer'] = 2
        elif wd_prefer.loc[i].watch_time < wd_prefer.loc[i].total_time * 0.75 :
            wd_prefer.loc[i,'prefer'] = 3
        else : 
            wd_prefer.loc[i,'prefer'] = 4

        
    except : 
        pass


In [99]:
wd_prefer.head()

profile_id           ss_id        log_time act_target_dtl  album_id  \
0           3  20220301115653  20220301115805        MKID049        15   
1           3  20220301115653  20220301115954        MKID049        16   
2           3  20220301115653  20220301120114        MKID049        17   
3           3  20220301115653  20220301120226        MKID049        18   
4           3  20220301115653  20220301120400        MKID049        19   

   watch_time  total_time  continuous_play  prefer  
0          46          46                1     4.0  
1         104         105                1     4.0  
2          76          76                1     4.0  
3          67          68                1     4.0  
4          90          90                0     4.0

In [110]:
### prefer에 nan있는지 확인

for i in wd_prefer.index 
    if wd_prefer.loc[i].prefer is not None == False : 
        print(i)

### 5. History data 유실부분 Watch data에서 append

#### 5-1 .history, watch data 확인

In [26]:
# 결측치 처리방법이 완전히 정해진게 아니므로 여기서 가격이 0 처리된 history data를 이용해서 작업함
# 결측치 처리방법이 정해지면 코드 뽑아서 수정

In [111]:
from datetime import datetime

In [112]:
hd.head()

profile_id           ss_id        log_time act_target_dtl  album_id  \
0           3  20220301115653  20220301115719        MKID003        15   
1           3  20220301115653  20220301115809        MKID003        16   
2           3  20220301115653  20220301115958        MKID003        17   
3           3  20220301115653  20220301120118        MKID003        18   
4           3  20220301115653  20220301120229        MKID003        19   

   payment continuous_play short_trailer      date    time  
0      0.0               Y             N  20220301  115719  
1      0.0               Y             N  20220301  115809  
2      0.0               Y             N  20220301  115958  
3      0.0               Y             N  20220301  120118  
4      0.0               Y             N  20220301  120229

In [113]:
wd.head()

profile_id           ss_id        log_time act_target_dtl  album_id  \
0           3  20220301115653  20220301115805        MKID049        15   
1           3  20220301115653  20220301115954        MKID049        16   
2           3  20220301115653  20220301120114        MKID049        17   
3           3  20220301115653  20220301120226        MKID049        18   
4           3  20220301115653  20220301120400        MKID049        19   

   watch_time  total_time  continuous_play  
0          46          46                1  
1         104         105                1  
2          76          76                1  
3          67          68                1  
4          90          90                0

In [114]:
print(hd.shape)
print(wd.shape)

(825692, 10)
(800740, 8)


### 5-2. history 유실데이터 확인

In [115]:
hd_pid = hd['profile_id'].value_counts(dropna=False).sort_index()
wd_pid = wd['profile_id'].value_counts(dropna=False).sort_index()

print("\n\nhd_pid\n", hd_pid)
print("\n\nwd_pid\n", wd_pid)



hd_pid
 3         21
5        543
7          2
12         7
16         3
        ... 
33022      2
33023     12
33026      1
33027     13
33032     79
Name: profile_id, Length: 8269, dtype: int64


wd_pid
 3         20
5        534
7          2
16         3
19         2
        ... 
33019      2
33023     10
33026      1
33027     12
33032    171
Name: profile_id, Length: 7658, dtype: int64


#### 문의에 나온 24번 profile 의 문제상황 확인

In [116]:


for i in range( hd.shape[0]) : 
    if hd.iloc[i].profile_id == 24 :
        print("\n--------\n")
        print("i : ", i )
        print(hd.iloc[i])
    else :
        pass
    
    
#loc : 전체 데이터 프레임에서 인덱스 이름이 0인 행만 추출
#iloc : 전체 데이터 프레임에서 0번쨔 행에 있는 값들만 추출


--------

i :  2722
profile_id                     24
ss_id              20220423195603
log_time           20220423195629
act_target_dtl            MKID003
album_id                     1869
payment                       0.0
continuous_play                 N
short_trailer                   N
date                     20220423
time                       195629
Name: 2944, dtype: object

--------

i :  2723
profile_id                     24
ss_id              20220423195603
log_time           20220423195946
act_target_dtl            MKID003
album_id                     1869
payment                       0.0
continuous_play                 N
short_trailer                   N
date                     20220423
time                       195946
Name: 2945, dtype: object

--------

i :  2724
profile_id                     24
ss_id              20220428003449
log_time           20220428003539
act_target_dtl            MKID003
album_id                     1869
payment                       0.0
c

In [117]:
for i in range( wd.shape[0]) : 
    if wd.iloc[i].profile_id == 24 :
        print("\n--------\n")
        print("i : ", i )
        print(wd.iloc[i])
    else :
        pass
    


--------

i :  2603
profile_id                     24
ss_id              20220423195603
log_time           20220423195940
act_target_dtl            MKID049
album_id                     1869
watch_time                    184
total_time                    502
continuous_play                 0
Name: 2823, dtype: object

--------

i :  2604
profile_id                     24
ss_id              20220423195603
log_time           20220423200207
act_target_dtl            MKID049
album_id                     1869
watch_time                    137
total_time                    502
continuous_play                 0
Name: 2824, dtype: object

--------

i :  2605
profile_id                     24
ss_id              20220428003449
log_time           20220428003524
act_target_dtl            MKID049
album_id                     3692
watch_time                     11
total_time                    172
continuous_play                 0
Name: 2825, dtype: object


####

In [243]:
#datetime 변환 함수(초까지)
datetime_format = "%Y%m%d%H%M%S"

def logtodate(log) :
    datetime_string = str(log)
    datetime_result = datetime.strptime(datetime_string, datetime_format)
    #print(datetime_result)
    return datetime_result

def logtodateint(log) :
    datetime_int = str(log)
    datetime_result = datetime.strptime(datetime_int, datetime_format)
    #print(datetime_result)
    return datetime_result

In [245]:
##logtime 비교해서 유실데이터 찾는 코드 

losscnt = 0
is_album_hd = True


for i in wd_pid.index : 
    tmp_wd = wd[wd['profile_id'] == i]
    tmp_hd = hd[hd['profile_id'] == i]
    
    
    #album으로한번 더 포문 돌려서 나누기 x2
    for j in tmp_wd.album_id : 
        try : 
            tmp_wd_album = tmp_wd[tmp_wd['album_id'] == j]
            tmp_hd_album = tmp_hd[tmp_hd['album_id'] == j]
        
        except :
            print("album_id : ", j ," 는 HD에 존재하지 않음")
            is_album_hd = False
            pass
        
        if is_album_hd == False :
            
            is_album_hd = True
            pass
        
        else : 
            
            for k in tmp_hd_album.index:
                log = logtodate(tmp_hd_album.log_time.loc[k])
                #tmp_hd.log_time.iloc[j] = round(logtodate(log),-1)
                #tmp_hd_album.log_time.loc[k] = logtodate(log) #datetime 형태
            
            for k in tmp_wd_album.index : 
                log = logtodateint(tmp_wd_album.log_time.loc[k])
                #log = logtodate(tmp_wd_album.log_time.loc[k])
                #tmp_wd.log_time.iloc[j] = round(logtodate(log),-1)
                #tmp_wd_album.log_time.loc[k] = logtodate(log) #datetime 형태
                #log = tmp_wd_album.log_time.loc[k]
                
                watchtime = tmp_wd.watch_time.loc[k]  #int형               
                #comparetime = log - timedelta(seconds=int(watchtime))
                ##4중포문 이대로도 괜찮은가
                
                for h in tmp_hd_album.index : 
                    cnt = 0 
                    
                    log_hd = logtodate(tmp_hd_album.log_time.loc[h])
                    
                    comparetime = log - log_hd #초 단위의 datetime
                    comparetime_round = round(comparetime.seconds,-1) #1의 자리수에서 반올림
                    if comparetime == watchtime or comparetime_round == watchtime  : 
                        cnt += 1
                        
                if cnt < 1 : 
                    print("---------")
                    print("k : ", k )
                    print(tmp_wd_album.loc[k])
                    losscnt += 1
        
        
    
    

            
        
print("loss cnt : ", losscnt)
        
        

---------
k :  0
profile_id                      3
ss_id              20220301115653
log_time           20220301115805
act_target_dtl            MKID049
album_id                       15
watch_time                     46
total_time                     46
continuous_play                 1
Name: 0, dtype: object
---------
k :  1
profile_id                      3
ss_id              20220301115653
log_time           20220301115954
act_target_dtl            MKID049
album_id                       16
watch_time                    104
total_time                    105
continuous_play                 1
Name: 1, dtype: object
---------
k :  2
profile_id                      3
ss_id              20220301115653
log_time           20220301120114
act_target_dtl            MKID049
album_id                       17
watch_time                     76
total_time                     76
continuous_play                 1
Name: 2, dtype: object
---------
k :  3
profile_id                      3
ss_id        

profile_id                      5
ss_id              20220321193733
log_time           20220321202117
act_target_dtl            MKID049
album_id                      128
watch_time                    116
total_time                    116
continuous_play                 1
Name: 224, dtype: object
---------
k :  226
profile_id                      5
ss_id              20220321193733
log_time           20220321202338
act_target_dtl            MKID049
album_id                      128
watch_time                    116
total_time                    116
continuous_play                 1
Name: 226, dtype: object
---------
k :  228
profile_id                      5
ss_id              20220321193733
log_time           20220321202627
act_target_dtl            MKID049
album_id                      128
watch_time                    116
total_time                    116
continuous_play                 1
Name: 228, dtype: object
---------
k :  230
profile_id                      5
ss_id             

profile_id                      5
ss_id              20220322200537
log_time           20220322201311
act_target_dtl            MKID049
album_id                       67
watch_time                      7
total_time                     92
continuous_play                 2
Name: 269, dtype: object
---------
k :  271
profile_id                      5
ss_id              20220322200537
log_time           20220322201420
act_target_dtl            MKID049
album_id                       67
watch_time                      3
total_time                     92
continuous_play                 2
Name: 271, dtype: object
---------
k :  63
profile_id                      5
ss_id              20220306142351
log_time           20220306145149
act_target_dtl            MKID049
album_id                      104
watch_time                     67
total_time                     67
continuous_play                 1
Name: 63, dtype: object
---------
k :  69
profile_id                      5
ss_id              20

profile_id                      5
ss_id              20220321193733
log_time           20220321201027
act_target_dtl            MKID049
album_id                      177
watch_time                     18
total_time                    661
continuous_play                 0
Name: 216, dtype: object
---------
k :  215
profile_id                      5
ss_id              20220321193733
log_time           20220321201002
act_target_dtl            MKID049
album_id                      182
watch_time                    178
total_time                    302
continuous_play                 0
Name: 215, dtype: object
---------
k :  200
profile_id                      5
ss_id              20220321193733
log_time           20220321194239
act_target_dtl            MKID049
album_id                      177
watch_time                    277
total_time                    661
continuous_play                 0
Name: 200, dtype: object
---------
k :  201
profile_id                      5
ss_id             

---------
k :  275
profile_id                      5
ss_id              20220322200537
log_time           20220322202148
act_target_dtl            MKID049
album_id                       86
watch_time                     78
total_time                     78
continuous_play                 1
Name: 275, dtype: object
---------
k :  282
profile_id                      5
ss_id              20220322200537
log_time           20220322203156
act_target_dtl            MKID049
album_id                       86
watch_time                     77
total_time                     78
continuous_play                 1
Name: 282, dtype: object
---------
k :  345
profile_id                      5
ss_id              20220326133022
log_time           20220326134551
act_target_dtl            MKID049
album_id                       86
watch_time                      2
total_time                     78
continuous_play                 2
Name: 345, dtype: object
---------
k :  532
profile_id                      5

...

profile_id                     22
ss_id              20220313213122
log_time           20220313231315
act_target_dtl            MKID049
album_id                      107
watch_time                     58
total_time                     58
continuous_play                 1
Name: 1523, dtype: object
---------
k :  1578
profile_id                     22
ss_id              20220318224528
log_time           20220318224715
act_target_dtl            MKID049
album_id                      107
watch_time                      4
total_time                     58
continuous_play                 0
Name: 1578, dtype: object
---------
k :  2580
profile_id                     22
ss_id              20220423083311
log_time           20220423085558
act_target_dtl            MKID049
album_id                      107
watch_time                     58
total_time                     58
continuous_play                 1
Name: 2580, dtype: object
---------
k :  2587
profile_id                     22
ss_id       

---------
k :  2736
profile_id                     22
ss_id              20220424214344
log_time           20220424231415
act_target_dtl            MKID049
album_id                     1017
watch_time                    585
total_time                    585
continuous_play                 1
Name: 2736, dtype: object
---------
k :  2780
profile_id                     22
ss_id              20220426213201
log_time           20220426213622
act_target_dtl            MKID049
album_id                     1017
watch_time                    236
total_time                    585
continuous_play                 1
Name: 2780, dtype: object
---------
k :  2786
profile_id                     22
ss_id              20220427212129
log_time           20220427212248
act_target_dtl            MKID049
album_id                     1017
watch_time                     44
total_time                    585
continuous_play                 0
Name: 2786, dtype: object
---------
k :  2574
profile_id                

---------
k :  2265
profile_id                     22
ss_id              20220412204751
log_time           20220412220547
act_target_dtl            MKID049
album_id                      955
watch_time                     45
total_time                    100
continuous_play                 0
Name: 2265, dtype: object
---------
k :  2682
profile_id                     22
ss_id              20220424214344
log_time           20220424221710
act_target_dtl            MKID049
album_id                      955
watch_time                    101
total_time                    102
continuous_play                 1
Name: 2682, dtype: object
---------
k :  2243
profile_id                     22
ss_id              20220412204751
log_time           20220412213455
act_target_dtl            MKID049
album_id                      956
watch_time                    199
total_time                    200
continuous_play                 1
Name: 2243, dtype: object
---------
k :  2260
profile_id                

---------
k :  2643
profile_id                     22
ss_id              20220424084809
log_time           20220424091607
act_target_dtl            MKID049
album_id                     1017
watch_time                    286
total_time                    585
continuous_play                 1
Name: 2643, dtype: object
---------
k :  2736
profile_id                     22
ss_id              20220424214344
log_time           20220424231415
act_target_dtl            MKID049
album_id                     1017
watch_time                    585
total_time                    585
continuous_play                 1
Name: 2736, dtype: object
---------
k :  2780
profile_id                     22
ss_id              20220426213201
log_time           20220426213622
act_target_dtl            MKID049
album_id                     1017
watch_time                    236
total_time                    585
continuous_play                 1
Name: 2780, dtype: object
---------
k :  2786
profile_id                

ValueError: unconverted data remains: 0

In [ ]:
#### 정제후 데이터로한거 유실데이터 20454개 

cnt = 0

for i in wd_pid.index : 
    tmp_wd = wd[wd['profile_id'] == i]
    tmp_hd = hd[hd['profile_id'] == i]
    
    
    #album으로한번 더 포문 돌려서 나누기 x2
    for j in tmp_wd.album_id : 
        
        tmp_wd_album = tmp_wd[tmp_wd['album_id'] == j]
        tmp_hd_album = tmp_hd[tmp_hd['album_id'] == j]
        
        if tmp_hd_album.index.shape[0] == 0 :
            cnt += 1 
            print(cnt ," : album_id ", j ," 는 HD profile_id ", i ,"에 존재하지 않음")
            is_album_hd = False
            

In [291]:
###정제 전 데이터로 한거

cnt = 0

for i in wd_pid.index : 
    tmp_wd = watch[watch['profile_id'] == i]
    tmp_hd = history[history['profile_id'] == i]
    
    
    #album으로한번 더 포문 돌려서 나누기 x2
    for j in tmp_wd.album_id : 
        
        tmp_wd_album = tmp_wd[tmp_wd['album_id'] == j]
        tmp_hd_album = tmp_hd[tmp_hd['album_id'] == j]
        
        if tmp_hd_album.index.shape[0] == 0 :
            cnt += 1 
            print(cnt ," : album_id ", j ," 는 HD profile_id ", i ,"에 존재하지 않음")
            is_album_hd = False
            

1  : album_id  3692  는 HD profile_id  24 에 존재하지 않음
2  : album_id  3669  는 HD profile_id  30 에 존재하지 않음
3  : album_id  849  는 HD profile_id  96 에 존재하지 않음
4  : album_id  3168  는 HD profile_id  179 에 존재하지 않음
5  : album_id  2989  는 HD profile_id  182 에 존재하지 않음
6  : album_id  2989  는 HD profile_id  182 에 존재하지 않음
7  : album_id  2989  는 HD profile_id  182 에 존재하지 않음
8  : album_id  2072  는 HD profile_id  182 에 존재하지 않음
9  : album_id  4324  는 HD profile_id  192 에 존재하지 않음
10  : album_id  4324  는 HD profile_id  192 에 존재하지 않음
11  : album_id  4324  는 HD profile_id  192 에 존재하지 않음
12  : album_id  6978  는 HD profile_id  192 에 존재하지 않음
13  : album_id  6978  는 HD profile_id  192 에 존재하지 않음
14  : album_id  6978  는 HD profile_id  192 에 존재하지 않음
15  : album_id  3853  는 HD profile_id  192 에 존재하지 않음
16  : album_id  3853  는 HD profile_id  192 에 존재하지 않음
17  : album_id  3853  는 HD profile_id  192 에 존재하지 않음
18  : album_id  3853  는 HD profile_id  192 에 존재하지 않음
19  : album_id  3853  는 HD profile_id  192 에 존재하지 않음
20  : 

326  : album_id  318  는 HD profile_id  302 에 존재하지 않음
327  : album_id  318  는 HD profile_id  302 에 존재하지 않음
328  : album_id  318  는 HD profile_id  302 에 존재하지 않음
329  : album_id  318  는 HD profile_id  302 에 존재하지 않음
330  : album_id  318  는 HD profile_id  302 에 존재하지 않음
331  : album_id  376  는 HD profile_id  302 에 존재하지 않음
332  : album_id  379  는 HD profile_id  302 에 존재하지 않음
333  : album_id  2107  는 HD profile_id  302 에 존재하지 않음
334  : album_id  200  는 HD profile_id  302 에 존재하지 않음
335  : album_id  5873  는 HD profile_id  302 에 존재하지 않음
336  : album_id  5877  는 HD profile_id  302 에 존재하지 않음
337  : album_id  5877  는 HD profile_id  302 에 존재하지 않음
338  : album_id  292  는 HD profile_id  390 에 존재하지 않음
339  : album_id  4203  는 HD profile_id  471 에 존재하지 않음
340  : album_id  162  는 HD profile_id  478 에 존재하지 않음
341  : album_id  4857  는 HD profile_id  478 에 존재하지 않음
342  : album_id  4843  는 HD profile_id  572 에 존재하지 않음
343  : album_id  6458  는 HD profile_id  572 에 존재하지 않음
344  : album_id  6458  는 HD profile_id

520  : album_id  5528  는 HD profile_id  717 에 존재하지 않음
521  : album_id  5528  는 HD profile_id  717 에 존재하지 않음
522  : album_id  6761  는 HD profile_id  717 에 존재하지 않음
523  : album_id  6761  는 HD profile_id  717 에 존재하지 않음
524  : album_id  6762  는 HD profile_id  717 에 존재하지 않음
525  : album_id  6762  는 HD profile_id  717 에 존재하지 않음
526  : album_id  5528  는 HD profile_id  717 에 존재하지 않음
527  : album_id  5528  는 HD profile_id  717 에 존재하지 않음
528  : album_id  6761  는 HD profile_id  717 에 존재하지 않음
529  : album_id  6761  는 HD profile_id  717 에 존재하지 않음
530  : album_id  6762  는 HD profile_id  717 에 존재하지 않음
531  : album_id  6762  는 HD profile_id  717 에 존재하지 않음
532  : album_id  5528  는 HD profile_id  717 에 존재하지 않음
533  : album_id  5528  는 HD profile_id  717 에 존재하지 않음
534  : album_id  5532  는 HD profile_id  717 에 존재하지 않음
535  : album_id  5532  는 HD profile_id  717 에 존재하지 않음
536  : album_id  5532  는 HD profile_id  717 에 존재하지 않음
537  : album_id  5532  는 HD profile_id  717 에 존재하지 않음
538  : album_id  10890  는 HD

674  : album_id  4843  는 HD profile_id  2335 에 존재하지 않음
675  : album_id  2071  는 HD profile_id  2341 에 존재하지 않음
676  : album_id  2458  는 HD profile_id  2341 에 존재하지 않음
677  : album_id  2458  는 HD profile_id  2341 에 존재하지 않음
678  : album_id  384  는 HD profile_id  2399 에 존재하지 않음
679  : album_id  384  는 HD profile_id  2399 에 존재하지 않음
680  : album_id  376  는 HD profile_id  2480 에 존재하지 않음
681  : album_id  376  는 HD profile_id  2480 에 존재하지 않음
682  : album_id  2024  는 HD profile_id  2480 에 존재하지 않음
683  : album_id  2024  는 HD profile_id  2480 에 존재하지 않음
684  : album_id  2025  는 HD profile_id  2480 에 존재하지 않음
685  : album_id  2025  는 HD profile_id  2480 에 존재하지 않음
686  : album_id  2026  는 HD profile_id  2480 에 존재하지 않음
687  : album_id  2026  는 HD profile_id  2480 에 존재하지 않음
688  : album_id  2026  는 HD profile_id  2480 에 존재하지 않음
689  : album_id  2026  는 HD profile_id  2480 에 존재하지 않음
690  : album_id  1436  는 HD profile_id  2482 에 존재하지 않음
691  : album_id  1436  는 HD profile_id  2482 에 존재하지 않음
692  : album_i

834  : album_id  4511  는 HD profile_id  2499 에 존재하지 않음
835  : album_id  4843  는 HD profile_id  2612 에 존재하지 않음
836  : album_id  1583  는 HD profile_id  2612 에 존재하지 않음
837  : album_id  4843  는 HD profile_id  2612 에 존재하지 않음
838  : album_id  2797  는 HD profile_id  2612 에 존재하지 않음
839  : album_id  2173  는 HD profile_id  2612 에 존재하지 않음
840  : album_id  1740  는 HD profile_id  2612 에 존재하지 않음
841  : album_id  4843  는 HD profile_id  2612 에 존재하지 않음
842  : album_id  4843  는 HD profile_id  2612 에 존재하지 않음
843  : album_id  498  는 HD profile_id  2612 에 존재하지 않음
844  : album_id  7632  는 HD profile_id  2612 에 존재하지 않음
845  : album_id  9106  는 HD profile_id  2612 에 존재하지 않음
846  : album_id  7632  는 HD profile_id  2612 에 존재하지 않음
847  : album_id  5974  는 HD profile_id  2664 에 존재하지 않음
848  : album_id  389  는 HD profile_id  2664 에 존재하지 않음
849  : album_id  388  는 HD profile_id  2664 에 존재하지 않음
850  : album_id  385  는 HD profile_id  2664 에 존재하지 않음
851  : album_id  385  는 HD profile_id  2664 에 존재하지 않음
852  : album_id

...

6467  : album_id  2071  는 HD profile_id  23538 에 존재하지 않음
6468  : album_id  2458  는 HD profile_id  23538 에 존재하지 않음
6469  : album_id  2458  는 HD profile_id  23538 에 존재하지 않음
6470  : album_id  2458  는 HD profile_id  23538 에 존재하지 않음
6471  : album_id  2458  는 HD profile_id  23538 에 존재하지 않음
6472  : album_id  2458  는 HD profile_id  23538 에 존재하지 않음
6473  : album_id  2458  는 HD profile_id  23538 에 존재하지 않음
6474  : album_id  2458  는 HD profile_id  23538 에 존재하지 않음
6475  : album_id  2072  는 HD profile_id  23538 에 존재하지 않음
6476  : album_id  0  는 HD profile_id  23538 에 존재하지 않음
6477  : album_id  2458  는 HD profile_id  23538 에 존재하지 않음
6478  : album_id  2458  는 HD profile_id  23538 에 존재하지 않음
6479  : album_id  2071  는 HD profile_id  23538 에 존재하지 않음
6480  : album_id  2458  는 HD profile_id  23538 에 존재하지 않음
6481  : album_id  11134  는 HD profile_id  23595 에 존재하지 않음
6482  : album_id  343  는 HD profile_id  23651 에 존재하지 않음
6483  : album_id  470  는 HD profile_id  23651 에 존재하지 않음
6484  : album_id  2514  는 HD profil

6633  : album_id  376  는 HD profile_id  27628 에 존재하지 않음
6634  : album_id  376  는 HD profile_id  27628 에 존재하지 않음
6635  : album_id  376  는 HD profile_id  27628 에 존재하지 않음
6636  : album_id  376  는 HD profile_id  27628 에 존재하지 않음
6637  : album_id  4529  는 HD profile_id  27649 에 존재하지 않음
6638  : album_id  10040  는 HD profile_id  27672 에 존재하지 않음
6639  : album_id  3163  는 HD profile_id  27672 에 존재하지 않음
6640  : album_id  3214  는 HD profile_id  27915 에 존재하지 않음
6641  : album_id  3214  는 HD profile_id  27915 에 존재하지 않음
6642  : album_id  2587  는 HD profile_id  27915 에 존재하지 않음
6643  : album_id  3293  는 HD profile_id  27915 에 존재하지 않음
6644  : album_id  4581  는 HD profile_id  27915 에 존재하지 않음
6645  : album_id  17247  는 HD profile_id  27915 에 존재하지 않음
6646  : album_id  17247  는 HD profile_id  27915 에 존재하지 않음
6647  : album_id  4585  는 HD profile_id  27915 에 존재하지 않음
6648  : album_id  4585  는 HD profile_id  27915 에 존재하지 않음
6649  : album_id  4585  는 HD profile_id  27915 에 존재하지 않음
6650  : album_id  20045  는 HD pr

6847  : album_id  16249  는 HD profile_id  31294 에 존재하지 않음
6848  : album_id  22309  는 HD profile_id  31294 에 존재하지 않음
6849  : album_id  22309  는 HD profile_id  31294 에 존재하지 않음
6850  : album_id  16246  는 HD profile_id  31294 에 존재하지 않음
6851  : album_id  16247  는 HD profile_id  31294 에 존재하지 않음
6852  : album_id  16247  는 HD profile_id  31294 에 존재하지 않음
6853  : album_id  2458  는 HD profile_id  31294 에 존재하지 않음
6854  : album_id  2107  는 HD profile_id  31294 에 존재하지 않음
6855  : album_id  2107  는 HD profile_id  31294 에 존재하지 않음
6856  : album_id  2107  는 HD profile_id  31294 에 존재하지 않음
6857  : album_id  2107  는 HD profile_id  31294 에 존재하지 않음
6858  : album_id  6145  는 HD profile_id  31294 에 존재하지 않음
6859  : album_id  6145  는 HD profile_id  31294 에 존재하지 않음
6860  : album_id  6145  는 HD profile_id  31294 에 존재하지 않음
6861  : album_id  6145  는 HD profile_id  31294 에 존재하지 않음
6862  : album_id  4485  는 HD profile_id  31294 에 존재하지 않음
6863  : album_id  4485  는 HD profile_id  31294 에 존재하지 않음
6864  : album_id  4485  는

7038  : album_id  4369  는 HD profile_id  31878 에 존재하지 않음
7039  : album_id  4369  는 HD profile_id  31878 에 존재하지 않음
7040  : album_id  4369  는 HD profile_id  31878 에 존재하지 않음
7041  : album_id  2458  는 HD profile_id  31878 에 존재하지 않음
7042  : album_id  2458  는 HD profile_id  31878 에 존재하지 않음
7043  : album_id  1879  는 HD profile_id  31878 에 존재하지 않음
7044  : album_id  2600  는 HD profile_id  31878 에 존재하지 않음
7045  : album_id  2600  는 HD profile_id  31878 에 존재하지 않음
7046  : album_id  1032  는 HD profile_id  31878 에 존재하지 않음
7047  : album_id  1032  는 HD profile_id  31878 에 존재하지 않음
7048  : album_id  14451  는 HD profile_id  31878 에 존재하지 않음
7049  : album_id  14451  는 HD profile_id  31878 에 존재하지 않음
7050  : album_id  15852  는 HD profile_id  31878 에 존재하지 않음
7051  : album_id  1033  는 HD profile_id  31878 에 존재하지 않음
7052  : album_id  15852  는 HD profile_id  31878 에 존재하지 않음
7053  : album_id  4415  는 HD profile_id  31878 에 존재하지 않음
7054  : album_id  4415  는 HD profile_id  31878 에 존재하지 않음
7055  : album_id  4366  는 H

7367  : album_id  172  는 HD profile_id  32759 에 존재하지 않음
7368  : album_id  6458  는 HD profile_id  32807 에 존재하지 않음
7369  : album_id  353  는 HD profile_id  32807 에 존재하지 않음
7370  : album_id  9452  는 HD profile_id  32807 에 존재하지 않음
7371  : album_id  6458  는 HD profile_id  32807 에 존재하지 않음
7372  : album_id  2027  는 HD profile_id  32957 에 존재하지 않음
7373  : album_id  3480  는 HD profile_id  32957 에 존재하지 않음
7374  : album_id  393  는 HD profile_id  32957 에 존재하지 않음
7375  : album_id  393  는 HD profile_id  32957 에 존재하지 않음
7376  : album_id  3012  는 HD profile_id  32957 에 존재하지 않음
7377  : album_id  1294  는 HD profile_id  32957 에 존재하지 않음
7378  : album_id  356  는 HD profile_id  32957 에 존재하지 않음
7379  : album_id  1469  는 HD profile_id  32957 에 존재하지 않음
7380  : album_id  3012  는 HD profile_id  32957 에 존재하지 않음
7381  : album_id  737  는 HD profile_id  32957 에 존재하지 않음
7382  : album_id  1294  는 HD profile_id  32957 에 존재하지 않음
7383  : album_id  3012  는 HD profile_id  32957 에 존재하지 않음
7384  : album_id  3012  는 HD profile_

In [280]:
hd[hd['profile_id']==33032]

profile_id           ss_id        log_time act_target_dtl  album_id  \
1005510       33032  20220426104174  20220426104334        MKID003      1367   
1005511       33032  20220426104174  20220426104353        MKID003       423   
1005512       33032  20220426104174  20220426104410        MKID003      1737   
1005513       33032  20220426104174  20220426104451        MKID003       320   
1005515       33032  20220426104174  20220426104536        MKID003       423   
...             ...             ...             ...            ...       ...   
1005643       33032  20220427155091  20220427155601        MKID003       381   
1005644       33032  20220427155091  20220427155611        MKID003       381   
1005645       33032  20220427155091  20220427155642        MKID003       381   
1005648       33032  20220427155839  20220427155810        MKID003       125   
1005649       33032  20220427155706  20220427155838        MKID003       125   

         payment continuous_play short_trailer      date    time  
1005510      0.0               Y             N  20220426  104334  
1005511      0.0               N             N  20220426  104353  
1005512      0.0               N             N  20220426  104410  
1005513      0.0               N             N  20220426  104451  
1005515      0.0               N             N  20220426  104536  
...          ...             ...           ...       ...     ...  
1005643      0.0               Y             N  20220427  155601  
1005644      0.0               Y             N  20220427  155611  
1005645      0.0               N             N  20220427  155642  
1005648      0.0               Y             N  20220427  155810  
1005649      0.0               Y             N  20220427  155838  

[79 rows x 10 columns]

In [281]:
wd[wd['profile_id']==33032]

profile_id           ss_id        log_time act_target_dtl  album_id  \
892623       33032  20220426104174  20220426104408        MKID049      1737   
892624       33032  20220426104174  20220426104439        MKID049      1737   
892625       33032  20220426104174  20220426104496        MKID049      1367   
892626       33032  20220426104174  20220426104512        MKID049       320   
892627       33032  20220426104174  20220426104520        MKID049       423   
...            ...             ...             ...            ...       ...   
892789       33032  20220427155091  20220427155653        MKID049       381   
892790       33032  20220427155091  20220427155694        MKID049       381   
892791       33032  20220427155839  20220427155826        MKID049       125   
892792       33032  20220427155706  20220427155836        MKID049       125   
892793       33032  20220427155839  20220427155897        MKID049       381   

        watch_time  total_time  continuous_play  
892623           2         134                0  
892624           2         135                0  
892625           3         117                0  
892626          11         120                0  
892627           5         121                0  
...            ...         ...              ...  
892789         463         464                1  
892790         462         463                1  
892791          10         520                0  
892792           6         521                0  
892793         462         464                1  

[171 rows x 8 columns]

In [290]:
history[history['profile_id'] == 33016].shape

(2, 8)

In [289]:
watch[watch['profile_id'] == 33016].shape

(34, 8)

In [293]:
ss = history[history['profile_id'] == 33032]
ss = ss[ss['album_id'] == 373] 

In [296]:
dd = watch[watch['profile_id'] == 33032]
dd = dd[dd['album_id'] == 373]

dd

profile_id           ss_id        log_time act_target_dtl  album_id  \
892633       33032  20220426104961  20220426104970        MKID049       373   
892634       33032  20220426104961  20220426104979        MKID049       373   
892635       33032  20220426104961  20220426105051        MKID049       373   
892636       33032  20220426104961  20220426105061        MKID049       373   
892751       33032  20220427145118  20220427145169        MKID049       373   
892765       33032  20220427150324  20220427150457        MKID049       373   
892766       33032  20220427150324  20220427150480        MKID049       373   
892767       33032  20220427150528  20220427150508        MKID049       373   
892768       33032  20220427150508  20220427150580        MKID049       373   
892779       33032  20220427155091  20220427155112        MKID049       373   

        watch_time  total_time  continuous_play  
892633           1          48                0  
892634         997         997                1  
892635         997         997                1  
892636           6          50                0  
892751         997         997                1  
892765           1          50                0  
892766         997         997                1  
892767           3          48                0  
892768         997         997                1  
892779           7          48                0